In [1]:
import osmium
import json
import pandas as pd
import geopandas as gpd 
from rasterstats import zonal_stats

### RailwayStation Centroid

In [ ]:
# 1. Read the railway station (previous data: see the parameter to be considered)

railway_station = gpd.read_file('/Users/sell/work/code_work/daina_project/data/input/dolnoslaskie/railway_station.geojson')

In [ ]:
railway_station.columns

Index(['full_id', 'osm_id', 'osm_type', 'railway', 'addr:city:simc', 'bus',
       'baby_feeding', 'air_conditioning', 'name:zh', 'historic:railway:ref',
       ...
       'opening_date', 'razed:railway', 'construction:platforms',
       'construction:railway', 'fixme', 'layer', 'path', 'x', 'y', 'geometry'],
      dtype='object', length=131)

In [ ]:
railway_station[['osm_id','osm_type','railway','x','y','geometry']]

osm_id osm_type  railway       x       y                   geometry
0    155479759     node  station  17.038  51.098  POINT (17.03795 51.09792)
1    241763683     node  station  17.084  51.143  POINT (17.08354 51.14255)
2    242360270     node  station  17.297  50.931  POINT (17.29743 50.93075)
3    248216807     node  station  17.034  50.609  POINT (17.03389 50.60865)
4    266565814     node  station  16.486  51.216  POINT (16.48597 51.21569)
..         ...      ...      ...     ...     ...                        ...
411       None     None     halt  15.798  50.862  POINT (15.79778 50.86237)
412       None     None     halt  15.794  50.887  POINT (15.79441 50.88682)
413       None     None     halt  16.255  51.215  POINT (16.25463 51.21501)
414       None     None     halt  16.510  50.612  POINT (16.50958 50.61205)
415       None     None     halt  16.621  50.693  POINT (16.62078 50.69278)

[416 rows x 6 columns]

In [19]:
# 2. make the new algorithm for taking the update data 

class RailwayToGeoJSON(osmium.SimpleHandler):
    def __init__(self, bbox=None):
        """
        bbox is optional. 
        If provided, it should be: (min_lat, min_lon, max_lat, max_lon)
        """
        super(RailwayToGeoJSON, self).__init__()
        self.features = []
        self.bbox = bbox

    def node(self, n):
        if 'railway' in n.tags and n.tags['railway'] == 'station':# this is optional > in['station', 'halt']
            lon = n.location.lon
            lat = n.location.lat
            
            # --- Optional Bounding Box Logic ---
            is_inside = True
            if self.bbox:
                min_lat, min_lon, max_lat, max_lon = self.bbox
                if not (min_lat <= lat <= max_lat and min_lon <= lon <= max_lon):
                    is_inside = False
            
            if is_inside:
                # 1. Convert tags to a readable dictionary
                all_tags = {tag.k: tag.v for tag in n.tags}
                
                # 2. Print to console to inspect the data
                station_name = all_tags.get('name', 'Unnamed')
                print(f"--- Station: {station_name} ---")
                print(json.dumps(all_tags, indent=2, ensure_ascii=False))
                print("-" * 30)
                
                feature = {
                    "type": "Feature",
                    "geometry": {
                        "type": "Point",
                        "coordinates": [lon, lat] #  "properties": all_tags
                    },
                    "properties": {
                        "osm_id": n.id,
                        "name": n.tags.get('name', 'null'),
                        "operator": n.tags.get ('operator','null'),
                        "railway": n.tags['railway'],
                        "x": lon,
                        "y": lat
                        
                    }
                }
                self.features.append(feature)



In [20]:
# --- Scenario 1: Using the Bounding Box (Dolnośląskie) ---
dolnoslaskie_bbox = (50.5, 14.5, 51.8, 17.8)
handler_with_bbox = RailwayToGeoJSON(bbox=dolnoslaskie_bbox)
handler_with_bbox.apply_file("/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/poland_260117.osm.pbf")

geojson_data = {
    "type": "FeatureCollection",
    "features": handler_with_bbox.features}
# 3. Save to file
output_path = "/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/railwayStation_centroid_dolnoslaski.geojson"
with open(output_path, 'w') as f:
    json.dump(geojson_data, f, indent=2)

# # --- Scenario 2: No Bounding Box (Whole File/Poland) ---
# handler_all = RailwayToGeoJSON(bbox=None)

--- Station: Wrocław Główny ---
{
  "alt_name": "Wrocław Główny Osobowy;Dworzec PKP Wrocław Główny",
  "name": "Wrocław Główny",
  "network": "PKP Polskie Linie Kolejowe S.A.",
  "operator": "PKP Polskie Linie Kolejowe",
  "operator:short": "PKP PLK",
  "public_transport": "station",
  "railway": "station",
  "railway:ref": "WG",
  "railway:ref:DB": "XPWR",
  "train": "yes",
  "uic_ref": "5100069",
  "wheelchair": "yes",
  "wikidata": "Q428443",
  "wikipedia": "pl:Wrocław Główny"
}
------------------------------
--- Station: Wrocław Sołtysowice ---
{
  "name": "Wrocław Sołtysowice",
  "old_name:de": "Breslau Schottwitz",
  "operator": "PKP Polskie Linie Kolejowe",
  "operator:short": "PKP PLK",
  "public_transport": "station",
  "railway": "station",
  "railway:ref": "WSł",
  "uic_ref": "5104139",
  "wikidata": "Q2529968",
  "wikipedia": "pl:Wrocław Sołtysowice"
}
------------------------------
--- Station: Oława ---
{
  "name": "Oława",
  "operator": "PKP Polskie Linie Kolejowe",
  "o

In [21]:
# read the updated data
railwayStation_centroid = gpd.read_file("/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/railwayStation_centroid_dolnoslaski.geojson")
railwayStation_centroid.head(5)

osm_id                 name                    operator  railway  \
0  155479759       Wrocław Główny  PKP Polskie Linie Kolejowe  station   
1  241763683  Wrocław Sołtysowice  PKP Polskie Linie Kolejowe  station   
2  242360270                Oława  PKP Polskie Linie Kolejowe  station   
3  248216807              Ziębice  PKP Polskie Linie Kolejowe  station   
4  249073484              Višňová             Správa železnic  station   

           x          y                   geometry  
0  17.037951  51.097916  POINT (17.03795 51.09792)  
1  17.083537  51.142548  POINT (17.08354 51.14255)  
2  17.297431  50.930748  POINT (17.29743 50.93075)  
3  17.033887  50.608650  POINT (17.03389 50.60865)  
4  15.028598  50.973291   POINT (15.0286 50.97329)

### Road Network

In [ ]:
## This class below only to extract the osm type== line ( road line only )

# class AllRoadsHandler(osmium.SimpleHandler):
#     def __init__(self, bbox=None):
#         super(AllRoadsHandler, self).__init__()
#         self.features = []
#         self.bbox = bbox # (min_lat, min_lon, max_lat, max_lon)
        
#         self.road_types = {
#             'motorway', 'motorway_link', 'trunk', 'trunk_link', 
#             'primary', 'primary_link', 'secondary', 'secondary_link', 
#             'tertiary', 'tertiary_link', 'unclassified', 'residential', 'service'
#         }

#     def way(self, w):
#         if 'highway' in w.tags and w.tags['highway'] in self.road_types:
#             try:
#                 # 1. Get all coordinates (vertices) for the road
#                 # coords is a list of [longitude, latitude]
#                 coords = [[n.lon, n.lat] for n in w.nodes]
                
#                 # 2. Extract specific start point
#                 start_x = coords[0][0]
#                 start_y = coords[0][1]
                
#                 # 3. Optional Bounding Box Check
#                 is_inside = True
#                 if self.bbox:
#                     min_lat, min_lon, max_lat, max_lon = self.bbox
#                     if not (min_lat <= start_y <= max_lat and min_lon <= start_x <= max_lon):
#                         is_inside = False
                
#                 if is_inside:
#                     # Convert ALL tags to a dictionary
#                     all_tags = {tag.k: tag.v for tag in w.tags}
                    
#                     # Add calculated properties to all_tags first
#                     all_tags["osm_id"] = w.id
#                     all_tags["x_start"] = start_x
#                     all_tags["y_start"] = start_y
#                     # Store the vertices as a list in properties
#                     all_tags["vertices"] = coords 
#                     # Store count of vertices (useful for analysis)
#                     all_tags["vertex_count"] = len(coords)

#                     # Inspect the data (Optional)
#                     # print(f"--- Road: {all_tags.get('name', 'Unnamed')} | Nodes: {len(coords)} ---")

#                     # Selection: define which tags to keep in the GeoJSON properties
#                     keys_to_keep = [
#                         'osm_id', 'name', 'highway', 'surface', 
#                         'x_start', 'y_start', 'vertex_count', 'vertices'
#                     ]
#                     selected_tags = {k: all_tags.get(k, 'null') for k in keys_to_keep}

#                     feature = {
#                         "type": "Feature",
#                         "geometry": {
#                             "type": "LineString",
#                             "coordinates": coords
#                         },
#                         "properties": selected_tags 
#                     }
#                     self.features.append(feature)

#             except osmium.InvalidLocationError:
#                 # Skip if nodes are missing from the PBF extract
#                 pass

# # --- How to Run ---

# # Example: Dolnośląskie BBox
# dolnoslaskie = (51.0, 16.8, 51.2, 17.2)

# # Initialize (Change to bbox=None to get all of Poland)
# handler = AllRoadsHandler(bbox=dolnoslaskie)

# # IMPORTANT: You must use locations=True for road coordinates!
# handler.apply_file("/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/poland_260117.osm.pbf", locations=True)


# # geojson data
# geojson_data = {
#     "type": "FeatureCollection",
#     "features": handler.features}

# # Save
# output_path = "/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/roadLine_network_dolnoslaski_1.geojson"
# with open(output_path, 'w') as f:
#     json.dump(geojson_data, f, indent=2)

# print(f"Extracted {len(handler.features)} road segments.")

In [ ]:
## this class below use to extract road line and convert into vertices

class RoadVertexHandler(osmium.SimpleHandler):
    def __init__(self, bbox=None):
        super(RoadVertexHandler, self).__init__()
        self.features = []
        self.bbox = bbox
        self.road_types = {
            'motorway', 'motorway_link', 'trunk', 'trunk_link', 
            'primary', 'primary_link', 'secondary', 'secondary_link', 
            'tertiary', 'tertiary_link', 'unclassified', 'residential', 'service'
        }

    def way(self, w):
        if 'highway' in w.tags and w.tags['highway'] in self.road_types:
            try:
                # 1. Extract all nodes/vertices from the way
                # We use a list of tuples (lon, lat)
                coords = [[n.lon, n.lat] for n in w.nodes]
                
                # 2. Capture all common tags once for duplication
                all_tags = {tag.k: tag.v for tag in w.tags}
                
                # 3. Iterate through every vertex to create individual "Point" rows
                for index, (lon, lat) in enumerate(coords):
                    
                    # 4. Optional BBox Check for the specific vertex
                    is_inside = True
                    if self.bbox:
                        min_lat, min_lon, max_lat, max_lon = self.bbox
                        if not (min_lat <= lat <= max_lat and min_lon <= lon <= max_lon):
                            is_inside = False
                    
                    if is_inside:
                        feature = {
                            "type": "Feature",
                            "geometry": {
                                "type": "Point",
                                "coordinates": [lon, lat]
                            },
                            "properties": {
                                "osm_id": w.id,
                                "name": all_tags.get('name', 'Unnamed'),
                                "highway": all_tags.get('highway', 'null'),
                                "surface": all_tags.get('surface', 'null'),
                                "vertex_index": index,  # Order of point in the road
                                "x":lon,
                                "y":lat,
                                "is_start": index == 0,
                                "is_end": index == len(coords) - 1
                            }
                        }
                        self.features.append(feature)
                        
            except osmium.InvalidLocationError:
                pass

# --- Configuration ---
# Lower Silesia BBox (South, West, North, East)
dolnoslaskie_bbox = (51.0, 16.8, 51.2, 17.2)

handler = RoadVertexHandler(bbox=dolnoslaskie_bbox)
input_pbf = "/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/poland_260117.osm.pbf"

print("Processing... converting road lines into individual vertex points.")
handler.apply_file(input_pbf, locations=True)

# Save to GeoJSON
output_data = {
    "type": "FeatureCollection",
    "features": handler.features
}

output_path = "/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/roadNetwork_centroid_dolnoslaskie.geojson"
with open(output_path, 'w') as f:
    json.dump(output_data, f)

print(f"Done! Created {len(handler.features)} vertex rows.")

Processing... converting road lines into individual vertex points.
Done! Created 290611 vertex rows.


In [2]:
roadLine_network = gpd.read_file("/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/roadNetwork_centroid_dolnoslaskie.geojson")
roadLine_network.head(5)


osm_id                  name  highway  surface  vertex_index          x  \
0  10737471  aleja Armii Krajowej  primary  asphalt             0  17.071156   
1  10737471  aleja Armii Krajowej  primary  asphalt             1  17.071027   
2  10737471  aleja Armii Krajowej  primary  asphalt             2  17.071017   
3  10737471  aleja Armii Krajowej  primary  asphalt             3  17.070992   
4  10737471  aleja Armii Krajowej  primary  asphalt             4  17.070980   

           y  is_start  is_end                   geometry  
0  51.085741      True   False  POINT (17.07116 51.08574)  
1  51.085970     False   False  POINT (17.07103 51.08597)  
2  51.085994     False   False  POINT (17.07102 51.08599)  
3  51.086050     False   False  POINT (17.07099 51.08605)  
4  51.086083     False   False  POINT (17.07098 51.08608)

### Solar Farm

In [ ]:
# class SolarFullHandler(osmium.SimpleHandler):
#     def __init__(self):
#         super(SolarFullHandler, self).__init__()
#         self.features = []

#     def is_solar(self, obj):
#         # Check for the specific tags you mentioned
#         plant_match = (obj.tags.get('power') == 'plant' and 
#                        obj.tags.get('plant:source') == 'solar' and 
#                        obj.tags.get('plant:method') == 'photovoltaic')
        
#         gen_match = obj.tags.get('generator:source') == 'solar'
        
#         return plant_match or gen_match

#     def node(self, n):
#         if self.is_solar(n):
#             self.add_feature(n, "Point", [n.location.lon, n.location.lat], "node")

#     def way(self, w):
#         # Handle ways that are not closed rings
#         if self.is_solar(w) and not w.is_closed():
#             try:
#                 coords = [[n.lon, n.lat] for n in w.nodes]
#                 self.add_feature(w, "LineString", coords, "way")
#             except osmium.InvalidLocationError:
#                 pass

#     def area(self, a):
#         # This handles closed Ways (polygons) and Relations (multipolygons)
#         if self.is_solar(a):
#             try:
#                 coords = []
#                 for ring in a.outer_rings():
#                     coords.append([[n.lon, n.lat] for n in ring])
                
#                 # GeoJSON Polygons coordinates
#                 self.add_feature(a, "Polygon", coords, "area")
#             except osmium.InvalidLocationError:
#                 pass

#     def add_feature(self, obj, geom_type, coords, osm_type):
#         # Areas use orig_id() because they could be derived from Ways or Relations
#         try:
#             obj_id = obj.orig_id() if hasattr(obj, 'orig_id') else obj.id
#         except:
#             obj_id = getattr(obj, 'id', 0)

#         feature = {
#             "type": "Feature",
#             "geometry": {
#                 "type": geom_type,
#                 "coordinates": coords
#             },
#             "properties": {
#                 "id": obj_id,
#                 "osm_type_extracted": osm_type,
#                 "type_tag": obj.tags.get('type', 'null'), # Usually for relations (multipolygon)
#                 "name": obj.tags.get('name', 'null'),
#                 "power": obj.tags.get('power', 'null'),
#                 "plant_method": obj.tags.get('plant:method', 'null'),
#                 "plant_source": obj.tags.get('plant:source', 'null'),
#                 "generator_source": obj.tags.get('generator:source', 'null'),
#                 "output_electricity": obj.tags.get('plant:output:electricity', obj.tags.get('generator:output:electricity', 'null'))
#             }
#         }
#         self.features.append(feature)

In [ ]:


# class SolarFullHandler(osmium.SimpleHandler):
#     def __init__(self, bbox=None):
#         super(SolarFullHandler, self).__init__()
#         self.features = []
#         self.bbox = bbox # Expects (min_lat, min_lon, max_lat, max_lon) or None

#     def is_solar(self, obj):
#         # Logic to identify solar infrastructure
#         plant_match = (obj.tags.get('power') == 'plant' and 
#                        obj.tags.get('plant:source') == 'solar' and 
#                        obj.tags.get('plant:method') == 'photovoltaic')
#         gen_match = obj.tags.get('generator:source') == 'solar'
#         return plant_match or gen_match

#     def check_bbox(self, lat, lon):
#         """If bbox is provided, check coordinates. If bbox is None, return True."""
#         if self.bbox is None:
#             return True
#         min_lat, min_lon, max_lat, max_lon = self.bbox
#         return min_lat <= lat <= max_lat and min_lon <= lon <= max_lon

#     def node(self, n):
#         if self.is_solar(n):
#             lon, lat = n.location.lon, n.location.lat
#             if self.check_bbox(lat, lon):
#                 self.add_feature(n, "Point", [lon, lat], "node")

#     def way(self, w):
#         if self.is_solar(w):
#             try:
#                 # Get coordinates for the shape
#                 coords = [[n.lon, n.lat] for n in w.nodes]
#                 # Check bbox using the first point of the line/polygon
#                 if self.check_bbox(coords[0][1], coords[0][0]):
#                     geom_type = "Polygon" if w.is_closed() else "LineString"
#                     # GeoJSON Polygons need an extra nested list
#                     final_coords = [coords] if w.is_closed() else coords
#                     self.add_feature(w, geom_type, final_coords, "way")
#             except osmium.InvalidLocationError:
#                 pass

#     def area(self, a):
#         if self.is_solar(a):
#             try:
#                 coords = []
#                 for ring in a.outer_rings():
#                     coords.append([[n.lon, n.lat] for n in ring])
                
#                 if coords and self.check_bbox(coords[0][0][1], coords[0][0][0]):
#                     self.add_feature(a, "Polygon", coords, "area")
#             except osmium.InvalidLocationError:
#                 pass

#     def add_feature(self, obj, geom_type, coords, osm_type):
#         try:
#             obj_id = obj.orig_id() if hasattr(obj, 'orig_id') else obj.id
#         except:
#             obj_id = getattr(obj, 'id', 0)

#         feature = {
#             "type": "Feature",
#             "geometry": {
#                 "type": geom_type,
#                 "coordinates": coords
#             },
#             "properties": {
#                 "osm_id": obj_id,
#                 "osm_type": osm_type,
#                 "name": obj.tags.get('name', 'null'),
#                 "power": obj.tags.get('power', 'null'),
#                 "plant_method": obj.tags.get('plant:method', 'null'),
#                 "plant_source": obj.tags.get('plant:source', 'null'),
#                 "output": obj.tags.get('plant:output:electricity', obj.tags.get('generator:output:electricity', 'null'))
#             }
#         }
#         self.features.append(feature)



In [ ]:
# class SolarFullHandler(osmium.SimpleHandler):
#     def __init__(self, bbox=None):
#         super(SolarFullHandler, self).__init__()
#         self.features = []
#         self.bbox = bbox
#         self.processed_ids = set()
#         self.all_found_tags = set()  # <--- Essential for discovery

#     def is_solar_farm(self, obj):
#         # Save every tag key seen in the data for the final printout
#         for tag in obj.tags:
#             self.all_found_tags.add(tag.k)
            
#         is_plant = obj.tags.get('power') in ['plant', 'generator']
#         is_solar = (obj.tags.get('plant:source') == 'solar' or 
#                     obj.tags.get('generator:source') == 'solar')
#         return is_plant and is_solar

#     def area(self, a):
#         if self.is_solar_farm(a):
#             try:
#                 orig_id = a.orig_id()
#                 if orig_id in self.processed_ids: return
                
#                 coords = []
#                 for ring in a.outer_rings():
#                     coords.append([[n.lon, n.lat] for n in ring])
                
#                 # Check bbox logic using the first point
#                 if coords:
#                     lon, lat = coords[0][0][0], coords[0][0][1]
#                     if self.bbox:
#                         s, w, n, e = self.bbox
#                         if not (s <= lat <= n and w <= lon <= e):
#                             return
                            
#                     self.add_feature(a, "Polygon", coords)
#                     self.processed_ids.add(orig_id)
#             except osmium.InvalidLocationError:
#                 pass

#     def add_feature(self, obj, geom_type, coords):
#         self.features.append({
#             "type": "Feature",
#             "geometry": {"type": geom_type, "coordinates": coords},
#             "properties": {
#                 "osm_id": obj.id,
#                 "name": obj.tags.get('name', 'null'),
#                 "power": obj.tags.get('power', 'null'),
#                 "plant_method": obj.tags.get('plant:method', obj.tags.get('generator:method', 'null')),
#                 "plant_source": obj.tags.get('plant:source', obj.tags.get('generator:source', 'null')),
#             }
#         })

#     def print_discovered_tags(self):
#         print("\n--- DISCOVERED TAG KEYS IN YOUR DATA ---")
#         if not self.all_found_tags:
#             print("No tags found. Check if is_solar_farm is being triggered.")
#         else:
#             for tag in sorted(self.all_found_tags):
#                 print(f"Key: {tag}")
#         print("----------------------------------------\n")

In [7]:
class SolarFarmToGeoJSON(osmium.SimpleHandler):
    def __init__(self, bbox=None):
        """
        bbox: (min_lat, min_lon, max_lat, max_lon)
        """
        super(SolarFarmToGeoJSON, self).__init__()
        self.features = []
        self.bbox = bbox
        self.processed_ids = set()

    def area(self, a):
        # 1. Filter for Solar Power Plants/Generators
        is_plant = a.tags.get('power') in ['plant', 'generator']
        is_solar = (a.tags.get('plant:source') == 'solar' or 
                    a.tags.get('generator:source') == 'solar')
        
        if is_plant and is_solar:
            try:
                # Get ID and prevent duplicates (Important for 'Area' objects)
                orig_id = a.orig_id()
                if orig_id in self.processed_ids:
                    return

                # 2. Build Geometry
                coords = []
                for ring in a.outer_rings():
                    coords.append([[n.lon, n.lat] for n in ring])

                if not coords:
                    return

                # 3. Bounding Box Check (using first point of first ring)
                lon, lat = coords[0][0][0], coords[0][0][1]
                is_inside = True
                if self.bbox:
                    s, w, n, e = self.bbox
                    if not (s <= lat <= n and w <= lon <= e):
                        is_inside = False

                if is_inside:
                    # --- DISCOVERY: Print all tags to console ---
                    # This allows you to see all available metadata
                    all_tags = {tag.k: tag.v for tag in a.tags}
                    farm_name = all_tags.get('name', 'Unnamed Solar Farm')
                    
                    print(f"\n[FOUND] OSM ID: {orig_id} | Name: {farm_name}")
                    print(json.dumps(all_tags, indent=4, ensure_ascii=False))
                    print("-" * 50)

                    # 4. Build the GeoJSON Feature
                    feature = {
                        "type": "Feature",
                        "geometry": {
                            "type": "Polygon",
                            "coordinates": coords
                        },
                        "properties": {
                            "osm_id": orig_id,
                            "name": farm_name,
                            "power": a.tags.get('power', 'null'),
                            "plant_method": a.tags.get('plant:method', a.tags.get('generator:method', 'null')),
                            "plant_source": a.tags.get('plant:source', a.tags.get('generator:source', 'null')),
                            "x": lon,
                            "y": lat
                        }
                    }
                    self.features.append(feature)
                    self.processed_ids.add(orig_id)

            except osmium.InvalidLocationError:
                pass

In [ ]:
# Lower Silesia BBox (South, West, North, East)
wroclaw_bbox = (51.0, 16.8, 51.2, 17.2)
handler = SolarFarmToGeoJSON(bbox=wroclaw_bbox)

input_pbf = "/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/poland_260117.osm.pbf"

print("Processing... extracting solar farm.")
handler.apply_file(input_pbf, locations=True)



# Save to GeoJSON
output_data = {
    "type": "FeatureCollection",
    "features": handler.features
}

output_path = "/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/solarFarm_centroid_dolnoslaskie_1.geojson"
with open(output_path, 'w') as f:
    json.dump(output_data, f)

print(f"Done! Created {len(handler.features)} solar farm centroid.")

Processing... extracting solar farm.

[FOUND] OSM ID: 816921563 | Name: Unnamed Solar Farm
{
    "colour": "black",
    "generator:method": "photovoltaic",
    "generator:output:electricity": "7 kW",
    "generator:source": "solar",
    "generator:type": "solar_photovoltaic_panel",
    "power": "generator",
    "start_date": "2020-06"
}
--------------------------------------------------

[FOUND] OSM ID: 935155476 | Name: Unnamed Solar Farm
{
    "generator:source": "solar",
    "power": "generator"
}
--------------------------------------------------

[FOUND] OSM ID: 1052144436 | Name: Unnamed Solar Farm
{
    "generator:method": "photovoltaic",
    "generator:output:electricity": "yes",
    "generator:source": "solar",
    "generator:type": "solar_photovoltaic_panel",
    "power": "generator"
}
--------------------------------------------------

[FOUND] OSM ID: 1063946545 | Name: Unnamed Solar Farm
{
    "generator:method": "photovoltaic",
    "generator:output:electricity": "yes",
  

### Land Use

In [3]:
import osmium
import json

class LandUseHandler(osmium.SimpleHandler):
    def __init__(self, bbox=None):
        super(LandUseHandler, self).__init__()
        self.features = []
        self.bbox = bbox

    def check_bbox(self, lat, lon):
        if self.bbox is None:
            return True
        min_lat, min_lon, max_lat, max_lon = self.bbox
        return min_lat <= lat <= max_lat and min_lon <= lon <= max_lon

    def area(self, a):
        if 'landuse' in a.tags:
            try:
                # 1. Extract Geometry
                coords = []
                for ring in a.outer_rings():
                    coords.append([[n.lon, n.lat] for n in ring])
                
                if not coords or not coords[0]:
                    return

                # 2. Bounding Box Check
                if self.check_bbox(coords[0][0][1], coords[0][0][0]):
                    
                    # 3. Handle IDs
                    try:
                        obj_id = a.orig_id()
                    except:
                        obj_id = getattr(a, 'id', 0)

                    # 4. CAPTURE & PRINT ALL TAGS (For your inspection only)
                    all_tags = {tag.k: tag.v for tag in a.tags}
                    print(f"--- FULL DATA INSPECTION [ID: {obj_id}] ---")
                    print(json.dumps(all_tags, indent=2, ensure_ascii=False))
                    print("-" * 40)

                    # 5. CREATE CLEAN PROPERTIES (Only what you want in the file)
                    clean_properties = {
                        "osm_id": obj_id,
                        "name": a.tags.get('name', 'null'),
                        "class": a.tags.get('landuse', 'null')
                    }
                    
                    # 6. Build Final Feature
                    feature = {
                        "type": "Feature",
                        "geometry": {
                            "type": "Polygon",
                            "coordinates": coords
                        },
                        "properties": clean_properties
                    }
                    
                    self.features.append(feature)
                    
            except osmium.InvalidLocationError:
                pass

# --- Execution ---
wroclaw_bbox = (51.0, 16.8, 51.2, 17.2)
handler = LandUseHandler(bbox=wroclaw_bbox)

input_pbf = "/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/poland_260117.osm.pbf"
output_path = "/Users/sell/work/code_work/daina_project/data/dataOSM/vector_data/wroclaw_landuse.geojson"

print("Starting extraction. Full tag details will print below...")
handler.apply_file(input_pbf, locations=True)

# Save to File
with open(output_path, 'w') as f:
    json.dump({"type": "FeatureCollection", "features": handler.features}, f)

print(f"\nExtraction Finished.")
print(f"Console: Displayed ALL tags for each object.")
print(f"File: Saved ONLY osm_id, name, and class to {output_path}")

Starting extraction. Full tag details will print below...
--- FULL DATA INSPECTION [ID: 17094291] ---
{
  "cemetery": "war_cemetery",
  "historic": "memorial",
  "image": "https://fotopolska.eu/767/767437/723/Wroclaw_Cmentarz_zolnierzy_polskich.jpg",
  "landuse": "cemetery",
  "memorial": "cemetery",
  "name": "Cmentarz Żołnierzy Polskich",
  "start_date": "1970",
  "url": "https://fotopolska.eu/9031,obiekt.html",
  "wheelchair": "no",
  "wikidata": "Q8510843",
  "wikipedia": "pl:Cmentarz Żołnierzy Polskich we Wrocławiu"
}
----------------------------------------
--- FULL DATA INSPECTION [ID: 17258441] ---
{
  "landuse": "residential"
}
----------------------------------------
--- FULL DATA INSPECTION [ID: 24354377] ---
{
  "landuse": "village_green"
}
----------------------------------------
--- FULL DATA INSPECTION [ID: 24469089] ---
{
  "description": "tutaj są teraz magazyny AMW na wynajem",
  "landuse": "commercial",
  "old_name": "4. Regionalna Baza Logistyczna Wojska Polskiego",

### Zonal Statistic

In [1]:
import geopandas as gpd
from rasterstats import gen_zonal_stats
import rasterio

# 1. Load your vector grid
grid_path = '/Users/sell/work/code_work/daina_project/data/dataOSM/raster_data/wroclaw_clipped.geojson'
grid = gpd.read_file(grid_path)

# 2. Path to your DNI raster
raster_path = '/Users/sell/work/code_work/daina_project/data/dataOSM/raster_data/wroclaw_dni.tif'

# 3. CRITICAL: Match CRS
# Rasterstats will crash or return 'None' if CRS is not identical
with rasterio.open(raster_path) as src:
    raster_crs = src.crs
    if grid.crs != raster_crs:
        print(f"Reprojecting grid to match raster...")
        grid = grid.to_crs(raster_crs)

# 4. Use gen_zonal_stats (The Generator version)
# This processes one polygon at a time to save RAM
print("Calculating zonal statistics...")
stats_generator = gen_zonal_stats(grid, raster_path, stats=['mean', 'max', 'min'])

# 5. Extract results from the generator
stats_list = list(stats_generator)

# 6. Map results back to the grid
grid['dni_mean'] = [s['mean'] for s in stats_list]
grid['dni_max'] = [s['max'] for s in stats_list]
grid['dni_min'] = [s['min'] for s in stats_list]

# 7. Export to GeoJSON
output_path = "/Users/sell/work/code_work/daina_project/data/dataOSM/raster_data/zonal_dni.geojson"
grid.to_file(output_path, driver='GeoJSON')

print(f"Success! Created: {output_path}")

: 